In [322]:
import pandas as pd
import json
from collections import defaultdict
import re
import numpy as np
import dataExtraction2
import dataExtraction3
import dataExtraction4

#### Con este bucle obtenemos los datos sobre la inicialización de todos los niveles jugados. PRUEBA

Si se han usado los pasos minimos:

In [323]:
#def porDefecto():
    #return defaultdict(lambda: {"tarjetasCreadas" : 0})

def extraerDatosTarjetas(rawData):
    erGameObject = re.compile(r'\bgame-object$\b')
    erInteracted = re.compile(r'\binteracted$\b')
    erCompleted = re.compile(r'\bcompleted$\b')
    erInitialized = re.compile(r'\binitialized$\b')
    erLevel = re.compile(r'\blevel$\b')
    erIdLevel = re.compile(r'/')
    
    dataCreadas = defaultdict(defaultdict)
    dataMovidas = defaultdict(defaultdict)
    dataEliminadas = defaultdict(defaultdict)
    dataAttach = defaultdict(defaultdict)
    dataDettach = defaultdict(defaultdict)
    dataDuplicate = defaultdict(defaultdict)
    dataDeclare = defaultdict(defaultdict)

    nivel = defaultdict()

    for evento in rawData:
        
        verb = evento["verb"]["id"]
        obj = evento["object"]["definition"]["type"]
        levelCode = 0

        #Empezamos nivel y lo guardamos
        if erLevel.search(obj) and erInitialized.search(verb):
            if "result" in evento:
                name = evento["actor"]["name"]
                levelCode = erIdLevel.split(evento["object"]["id"])[-1]
                nivel[name] = levelCode

        elif erGameObject.search(obj) : #Si el objeto de la acción es un objecto
            name = evento["actor"]["name"]

            if erInteracted.search(verb):
                    
                    try:
                        if nivel[name] != "editor_level":
                            #print(evento)
                                bloque = evento["result"]["extensions"]["block_type"]
                                accion = evento["result"]["extensions"]["action"]
                                levelCode = nivel[name]

                                if accion == "create":
                                    if levelCode not in dataCreadas[name]:
                                        dataCreadas[name][levelCode] = defaultdict()
                                        
                                    if bloque in dataCreadas[name][levelCode]:
                                            dataCreadas[name][levelCode][bloque] += 1
                                    else:
                                        dataCreadas[name][levelCode][bloque] = 1

                                elif accion == "move":
                                    if levelCode not in dataMovidas[name]:
                                        dataMovidas[name][levelCode] = defaultdict()
 
                                    if evento["result"]["extensions"]["block_type"] in dataMovidas[name][levelCode]:
                                            dataMovidas[name][levelCode][bloque] += 1
                                    else:
                                        dataMovidas[name][levelCode][bloque] = 1

                                elif accion == "remove":
                                    if levelCode not in dataEliminadas[name]:
                                        dataEliminadas[name][levelCode] = defaultdict()
                                    if evento["result"]["extensions"]["block_type"] in dataEliminadas[name][levelCode]:
                                            dataEliminadas[name][levelCode][bloque] += 1
                                    else:
                                        dataEliminadas[name][levelCode][bloque] = 1

                                elif accion == "attach" or accion == "attach_to_input" or accion == "attach_to_bottom" or accion == "attach_to_top":
                                    if levelCode not in dataAttach[name]:
                                        dataAttach[name][levelCode] = defaultdict()
                                    if evento["result"]["extensions"]["block_type"] in dataAttach[name][levelCode]:
                                            dataAttach[name][levelCode][bloque] += 1
                                    else:
                                        dataAttach[name][levelCode][bloque] = 1
                                
                                elif accion == "dettach":
                                    if levelCode not in dataDettach[name]:
                                        dataDettach[name][levelCode] = defaultdict()
                                    if evento["result"]["extensions"]["block_type"] in dataDettach[name][levelCode]:
                                            dataDettach[name][levelCode][bloque] += 1
                                    else:
                                        dataDettach[name][levelCode][bloque] = 1

                                elif accion == "duplicate":
                                    if levelCode not in dataDuplicate[name]:
                                        dataDuplicate[name][levelCode] = defaultdict()
                                    if evento["result"]["extensions"]["block_type"] in dataDuplicate[name][levelCode]:
                                            dataDuplicate[name][levelCode][bloque] += 1
                                    else:
                                        dataDuplicate[name][levelCode][bloque] = 1
                        
                                elif accion == "declare":
                                    if levelCode not in dataDeclare[name]:
                                        dataDeclare[name][levelCode] = defaultdict()
                                    if evento["result"]["extensions"]["block_type"] in dataDeclare[name][levelCode]:
                                        dataDeclare[name][levelCode][bloque] += 1
                                    else:
                                        dataDeclare[name][levelCode][bloque] = 1

                    except KeyError:
                        pass               

    return dataCreadas, dataMovidas, dataEliminadas, dataAttach, dataDettach, dataDuplicate, dataDeclare 

In [379]:
def mediaTarjetas(data):
    mediaTarjeta = defaultdict(defaultdict)
    numero = defaultdict(defaultdict)
    listaValores = defaultdict(defaultdict)

    for name in data:
        for level in data[name]:
            for bloque in data[name][level]:
                if data[name][level][bloque] in mediaTarjeta[level]:
                    mediaTarjeta[level][bloque] += float(data[name][level][bloque])
                    numero[level][bloque] += 1
                    listaValores[level][bloque].append(float(data[name][level][bloque]))
                else:
                    mediaTarjeta[level][bloque] = float(data[name][level][bloque])
                    numero[level][bloque] = 1
                    listaValores[level][bloque] = [float(data[name][level][bloque])]

    for level in mediaTarjeta:
        for bloque in mediaTarjeta[level]:
            mediaTarjeta[level][bloque] = float(mediaTarjeta[level][bloque]) / float(numero[level][bloque])
    
    return mediaTarjeta, listaValores
            
            

                

In [380]:
"""#Laseres
def porDefecto():
    return defaultdict(lambda: {"laserCreados" : 0, "laserMovidos" : 0, "laserEliminados" : 0})

def extraerDatosLaseres(rawData):
    erGameObject = re.compile(r'\bgame-object$\b')
    erInteracted = re.compile(r'\binteracted$\b')
    
    data = defaultdict(porDefecto)

    for evento in rawData:
        
        verb = evento["verb"]["id"]
        obj = evento["object"]["definition"]["type"]
        if erGameObject.search(obj) : #Si el objeto de la acción es un objecto
            name = evento["actor"]["name"]

            if erInteracted.search(verb):
                print(evento)
                try:
                    dataExtraction3.anadirAlDiccionario(data, evento, name)
                except KeyError:
                    pass

    return data"""

'#Laseres\ndef porDefecto():\n    return defaultdict(lambda: {"laserCreados" : 0, "laserMovidos" : 0, "laserEliminados" : 0})\n\ndef extraerDatosLaseres(rawData):\n    erGameObject = re.compile(r\'\x08game-object$\x08\')\n    erInteracted = re.compile(r\'\x08interacted$\x08\')\n    \n    data = defaultdict(porDefecto)\n\n    for evento in rawData:\n        \n        verb = evento["verb"]["id"]\n        obj = evento["object"]["definition"]["type"]\n        if erGameObject.search(obj) : #Si el objeto de la acción es un objecto\n            name = evento["actor"]["name"]\n\n            if erInteracted.search(verb):\n                print(evento)\n                try:\n                    dataExtraction3.anadirAlDiccionario(data, evento, name)\n                except KeyError:\n                    pass\n\n    return data'

In [381]:
"""#Retry button
def porDefecto():
    return defaultdict(lambda: {"botonRetryUsado" : 0})

def extraerDatosBoton(rawData):
    erGameObject = re.compile(r'\bgame-object$\b')
    erInteracted = re.compile(r'\binteracted$\b')
    erButton = re.compile(r'\bretry_button$\b')
    
    data = defaultdict(porDefecto)

    for evento in rawData:
        
        verb = evento["verb"]["id"]
        obj = evento["object"]["definition"]["type"]
        if erGameObject.search(obj) : #Si el objeto de la acción es un objecto
            name = evento["actor"]["name"]

            if erInteracted.search(verb):
                print(evento)
                if erButton.search(evento["object"]["id"]):
                    
                    try:
                        dataExtraction4.anadirAlDiccionario(data, evento, name)
                    except KeyError:
                        pass

    return data """

'#Retry button\ndef porDefecto():\n    return defaultdict(lambda: {"botonRetryUsado" : 0})\n\ndef extraerDatosBoton(rawData):\n    erGameObject = re.compile(r\'\x08game-object$\x08\')\n    erInteracted = re.compile(r\'\x08interacted$\x08\')\n    erButton = re.compile(r\'\x08retry_button$\x08\')\n    \n    data = defaultdict(porDefecto)\n\n    for evento in rawData:\n        \n        verb = evento["verb"]["id"]\n        obj = evento["object"]["definition"]["type"]\n        if erGameObject.search(obj) : #Si el objeto de la acción es un objecto\n            name = evento["actor"]["name"]\n\n            if erInteracted.search(verb):\n                print(evento)\n                if erButton.search(evento["object"]["id"]):\n                    \n                    try:\n                        dataExtraction4.anadirAlDiccionario(data, evento, name)\n                    except KeyError:\n                        pass\n\n    return data '

In [382]:
"""import pandas as pd
import matplotlib as mpl
from matplotlib import cm
import matplotlib.pyplot as plt
from mpl_toolkits import mplot3d
from mpl_toolkits.mplot3d import Axes3D
import json
from collections import defaultdict
import re
import dataExtraction2

def extraerDatosTarjetas(rawData):
    erGameObject = re.compile(r'\bgame-object$\b')
    erInteracted = re.compile(r'\binteracted$\b')
    
    data = defaultdict(porDefecto)

    for evento in rawData:
        verb = evento["verb"]["id"]
        obj = evento["object"]["definition"]["type"]
        if erGameObject.search(obj) : #Si el objeto de la acción es un objecto
            name = evento["actor"]["name"]

            if erInteracted.search(verb):
                try:
                    levelCode = evento["result"]["extensions"]["level"]
                    dataExtraction2.anadirAlDiccionario(data, evento, name, levelCode)
                except KeyError:
                    pass

    return data            

%matplotlib widget

JSONFile = open('traces_Articoding_Escolapias.json')
rawData = json.load(JSONFile)
data = extraerDatosTarjetas(rawData)

# Creamos o entorno
fig = plt.figure()  # Creamos unha figura (contenedor para elementos a debuxar)
ax = fig.add_subplot(projection='3d')  # Engadimos un Axes á figura (contén os elementos do debuxo)
plt.xlabel("attack")  # Nombramos os eixos
plt.ylabel("hp")

# Debuxamos o scatter
ax.scatter(data['gqoj'][0]["tarjetasCreadas"], data['gqoj'][0]["tarjetasMovidas"], data['gqoj'][0]["tarjetasEliminadas"])

plt.show()"""

'import pandas as pd\nimport matplotlib as mpl\nfrom matplotlib import cm\nimport matplotlib.pyplot as plt\nfrom mpl_toolkits import mplot3d\nfrom mpl_toolkits.mplot3d import Axes3D\nimport json\nfrom collections import defaultdict\nimport re\nimport dataExtraction2\n\ndef extraerDatosTarjetas(rawData):\n    erGameObject = re.compile(r\'\x08game-object$\x08\')\n    erInteracted = re.compile(r\'\x08interacted$\x08\')\n    \n    data = defaultdict(porDefecto)\n\n    for evento in rawData:\n        verb = evento["verb"]["id"]\n        obj = evento["object"]["definition"]["type"]\n        if erGameObject.search(obj) : #Si el objeto de la acción es un objecto\n            name = evento["actor"]["name"]\n\n            if erInteracted.search(verb):\n                try:\n                    levelCode = evento["result"]["extensions"]["level"]\n                    dataExtraction2.anadirAlDiccionario(data, evento, name, levelCode)\n                except KeyError:\n                    pass\n\n  

In [383]:
#%%
"""pokemon = pd.read_csv('pokemon.csv',  # Cargamos o csv
                       delimiter=',',
                       header=0)
pokemon.drop(['abilities','against_bug', 'against_dark', 'against_dragon', 'against_electric', 'against_fairy', 'against_fight', 'against_fire', 'against_flying', 'against_ghost', 'against_grass', 'against_ground', 'against_ice', 'against_normal', 'against_poison', 'against_psychic', 'against_rock', 'against_steel', 'against_water', 'base_egg_steps', 'base_happiness', 'base_total', 'capture_rate', 'classfication', 'experience_growth', 'height_m', 'japanese_name', 'name', 'percentage_male', 'pokedex_number', 'type1', 'type2', 'weight_kg', 'generation', 'sp_attack', 'sp_defense', 'defense', 'is_legendary'], axis = 'columns', inplace=True)

%matplotlib widget

# Creamos o entorno
fig = plt.figure()  # Creamos unha figura (contenedor para elementos a debuxar)
ax = fig.add_subplot(projection='3d')  # Engadimos un Axes á figura (contén os elementos do debuxo)
plt.xlabel("attack")  # Nombramos os eixos
plt.ylabel("hp")

# Debuxamos o scatter
ax.scatter(pokemon['attack'], pokemon['hp'], pokemon['speed'])

plt.show()"""


'pokemon = pd.read_csv(\'pokemon.csv\',  # Cargamos o csv\n                       delimiter=\',\',\n                       header=0)\npokemon.drop([\'abilities\',\'against_bug\', \'against_dark\', \'against_dragon\', \'against_electric\', \'against_fairy\', \'against_fight\', \'against_fire\', \'against_flying\', \'against_ghost\', \'against_grass\', \'against_ground\', \'against_ice\', \'against_normal\', \'against_poison\', \'against_psychic\', \'against_rock\', \'against_steel\', \'against_water\', \'base_egg_steps\', \'base_happiness\', \'base_total\', \'capture_rate\', \'classfication\', \'experience_growth\', \'height_m\', \'japanese_name\', \'name\', \'percentage_male\', \'pokedex_number\', \'type1\', \'type2\', \'weight_kg\', \'generation\', \'sp_attack\', \'sp_defense\', \'defense\', \'is_legendary\'], axis = \'columns\', inplace=True)\n\n%matplotlib widget\n\n# Creamos o entorno\nfig = plt.figure()  # Creamos unha figura (contenedor para elementos a debuxar)\nax = fig.add_sub

In [384]:
JSONFile = open('trazasOrdenadas.json')
rawData = json.load(JSONFile)
dataCreadas, dataMovidas, dataEliminadas, dataAttach, dataDettach, dataDuplicate, dataDeclare = extraerDatosTarjetas(rawData)
#data = extraerDatosLaseres(rawData)
#data = extraerDatosBoton(rawData)
pd.DataFrame(dataCreadas)

JSONFile.close()

pd.options.display.max_columns = None
pd.set_option('display.max_colwidth', None)
#pd.DataFrame(data)

pd.DataFrame(dataCreadas)

gqoj  \
tutorials_2        {'procedures_callreturn': 1, 'procedures_callnoreturn': 2, 'procedures_defreturn': 2, 'procedures_defnoreturn': 1, 'start_start': 1}   
variables_3                                                                                                                          {'math_number': 1}   
variables_4                                                                                                                        {'variables_get': 1}   
variables_5                                                                                                                                         NaN   
variables_6                                                                                                                                         NaN   
variables_7                                                                                                                                         NaN   
variables_8                                                                                                                                         NaN   
variables_9                                                                                                                                         NaN   
types_1                                                                                                                                             NaN   
types_2                                                                                                                                             NaN   
types_3                                                                                                                                             NaN   
types_4                                                                                                                                             NaN   
types_5                                                                                                                                             NaN   
types_6                                                                                                                                             NaN   
types_7                                                                                                                                             NaN   
types_8                                                                                                                                             NaN   
types_9                                                                                                                                             NaN   
basic_operators_2                                                                                                                                   NaN   
basic_operators_3                                                                                                                                   NaN   
basic_operators_4                                                                                                                                   NaN   
basic_operators_5                                                                                                                                   NaN   
basic_operators_6                                                                                                                                   NaN   
basic_operators_7                                                                                                                                   NaN   
loops_1                                                                                                                                             NaN   
loops_2                                                                                                                                             NaN   
loops_3                                                                                                              

In [385]:
mediaCreadas, listaCreadas = mediaTarjetas(dataCreadas)
pd.DataFrame(mediaCreadas)

tutorials_2  variables_3  variables_4  \
procedures_callreturn                    1.0          NaN          NaN   
procedures_callnoreturn                  2.0          NaN          NaN   
procedures_defreturn                     2.0          NaN          NaN   
procedures_defnoreturn                   1.0          NaN          NaN   
start_start                              1.0          NaN          1.0   
math_number                              NaN          1.0          NaN   
movement_move_laser                      NaN          2.0          NaN   
variables_get                            NaN          3.0          2.0   
movement_rotate_laser                    NaN          1.0          NaN   
variables_set                            NaN          NaN          1.0   
logic_ifelse                             NaN          NaN          1.0   
math_arithmetic                          NaN          NaN          1.0   
movement_rotate                          NaN          NaN          NaN   
movement_move                            NaN          NaN          NaN   
movement_laser_change_intensity          NaN          NaN          NaN   
text                                     NaN          NaN          NaN   
movement_activate_door                   NaN          NaN          NaN   
logic_boolean                            NaN          NaN          NaN   
logic_compare                            NaN          NaN          NaN   
logic_cells_occupied                     NaN          NaN          NaN   
logic_negate                             NaN          NaN          NaN   

                                 variables_5  variables_6  variables_7  \
procedures_callreturn                    NaN          NaN          NaN   
procedures_callnoreturn                  NaN          NaN          NaN   
procedures_defreturn                     NaN          NaN          NaN   
procedures_defnoreturn                   NaN          NaN          NaN   
start_start                              NaN          NaN          1.0   
math_number                              1.0          1.0          NaN   
movement_move_laser                      1.0          4.0          2.0   
variables_get                            5.0          5.0          3.0   
movement_rotate_laser                    1.0          1.0          1.0   
variables_set                            1.0          2.0          1.0   
logic_ifelse                             NaN          NaN          NaN   
math_arithmetic                          NaN          NaN          NaN   
movement_rotate                          NaN          1.0          NaN   
movement_move                            NaN          NaN          NaN   
movement_laser_change_intensity          NaN          NaN          NaN   
text                                     NaN          NaN          NaN   
movement_activate_door                   NaN          NaN          NaN   
logic_boolean                            NaN          NaN          NaN   
logic_compare                            NaN          NaN          NaN   
logic_cells_occupied                     NaN          NaN          NaN   
logic_negate                             NaN          NaN          NaN   

                                 variables_8  variables_9  types_1  types_2  \
procedures_callreturn                    NaN          NaN      NaN      NaN   
procedures_callnoreturn                  NaN          NaN      NaN      NaN   
procedures_defreturn                     NaN          NaN      NaN      NaN   
procedures_defnoreturn                   NaN          NaN      NaN      NaN   
start_start                              NaN          1.0      NaN      NaN   
math_number                              1.0          1.0      NaN      1.0   
movement_move_laser                      4.0          2.0      1.0      NaN   
variables_get                            3.0          3.0      2.0      1.0   
movement_rotate_laser                    NaN          1.0      1

In [386]:
def Outliers(data, lista):

    outliers = defaultdict(defaultdict)
    
    for name in data:
        for level in data[name]:
            for bloque in data[name][level]:
                lista[level][bloque].sort(key=lambda x: x)
                q3=np.quantile(lista[level][bloque], 0.75)
                q1=np.quantile(lista[level][bloque], 0.25)
                if data[name][level][bloque] > q3+(1.5*(q3-q1)):
                    if level not in outliers[name]:
                        outliers[name][level] = defaultdict()
                    outliers[name][level] = {bloque + ": " + str(data[name][level][bloque])}

    return outliers

In [387]:
outliersCreadas = Outliers(dataCreadas, listaCreadas)
pd.DataFrame(outliersCreadas)

pbgky                 auvqa  \
variables_5                  {math_number: 2}    {variables_set: 2}   
variables_6        {movement_rotate_laser: 2}                   NaN   
types_3                    {variables_get: 4}    {variables_get: 8}   
types_4                    {movement_move: 2}      {math_number: 2}   
types_5                  {movement_rotate: 2}    {variables_get: 7}   
types_7                    {variables_get: 7}                   NaN   
types_8                  {movement_rotate: 2}                   NaN   
types_9                    {variables_get: 7}                   NaN   
variables_9                               NaN    {variables_get: 5}   
types_6                                   NaN  {movement_rotate: 2}   
variables_4                               NaN                   NaN   
variables_7                               NaN                   NaN   
variables_8                               NaN                   NaN   
basic_operators_3                         NaN                   NaN   
basic_operators_4                         NaN                   NaN   
basic_operators_7                         NaN                   NaN   
loops_1                                   NaN                   NaN   
loops_2                                   NaN                   NaN   
loops_3                                   NaN                   NaN   
basic_operators_2                         NaN                   NaN   
basic_operators_5                         NaN                   NaN   
types_2                                   NaN                   NaN   
variables_3                               NaN                   NaN   
types_1                                   NaN                   NaN   
basic_operators_6                         NaN                   NaN   

                                eprdu               gcpze               loemd  \
variables_5        {variables_set: 2}  {variables_set: 2}  {variables_set: 2}   
variables_6                       NaN                 NaN                 NaN   
types_3            {variables_get: 4}  {variables_get: 4}  {variables_get: 5}   
types_4            {variables_get: 8}  {variables_get: 8}  {variables_get: 8}   
types_5                     {text: 3}  {movement_move: 2}           {text: 3}   
types_7                           NaN                 NaN                 NaN   
types_8                           NaN                 NaN  {variables_set: 3}   
types_9              {math_number: 2}  {variables_set: 3}                 NaN   
variables_9                       NaN                 NaN                 NaN   
types_6                           NaN                 NaN                 NaN   
variables_4        {variables_get: 3}                 NaN  {variables_set: 2}   
variables_7        {variables_get: 5}                 NaN                 NaN   
variables_8        {variables_get: 4}                 NaN    {math_number: 2}   
basic_operators_3  {variables_get: 5}  {variables_get: 6}                 NaN   
basic_operators_4  {variables_get: 8}  {movement_move: 4}                 NaN   
basic_operators_7           {text: 2}           {text: 2}                 NaN   
loops_1            {variables_get: 8}  {variables_get: 2}                 NaN   
loops_2            {variables_get: 4}  {variables_get: 4}                 NaN   
loops_3            {variables_get: 6}  {variables_get: 6}                 NaN   
basic_operators_2                 NaN                 NaN                 NaN   
basic_operators_5                 NaN                 NaN                 NaN   
types_2                           NaN                 NaN                 NaN   
variables_3                       NaN                 NaN                 NaN   
types_1                           NaN                 NaN                 NaN   
basic_operators_6                 NaN                 NaN                 NaN   

                                  qeqyj                 uzzpo  \
variables_5          

In [388]:
pd.DataFrame(dataMovidas)

gqoj  \
tutorials_2        {'procedures_callreturn': 1, 'procedures_callnoreturn': 2, 'procedures_defreturn': 2, 'procedures_defnoreturn': 1, 'start_start': 1}   
variables_4                                                                                                                                         NaN   
variables_5                                                                                                                                         NaN   
variables_6                                                                                                                                         NaN   
variables_9                                                                                                                                         NaN   
types_4                                                                                                                                             NaN   
types_5                                                                                                                                             NaN   
types_6                                                                                                                                             NaN   
types_7                                                                                                                                             NaN   
types_8                                                                                                                                             NaN   
types_9                                                                                                                                             NaN   
types_3                                                                                                                                             NaN   
tutorials_4                                                                                                                                         NaN   
variables_7                                                                                                                                         NaN   
variables_8                                                                                                                                         NaN   
types_2                                                                                                                                             NaN   
variables_2                                                                                                                                         NaN   
variables_3                                                                                                                                         NaN   
types_1                                                                                                                                             NaN   
basic_operators_2                                                                                                                                   NaN   
basic_operators_3                                                                                                                                   NaN   
basic_operators_4                                                                                                                                   NaN   
basic_operators_7                                                                                                                                   NaN   
loops_3                                                                                                                                             NaN   
basic_operators_5                                                                                                                                   NaN   
loops_1                                                                                                              

In [389]:
mediaMovidas, listaMovidas = mediaTarjetas(dataMovidas)
pd.DataFrame(mediaMovidas)

tutorials_2  variables_4  variables_5  \
procedures_callreturn                    1.0          NaN          NaN   
procedures_callnoreturn                  2.0          NaN          NaN   
procedures_defreturn                     2.0          NaN          NaN   
procedures_defnoreturn                   1.0          NaN          NaN   
start_start                              1.0          1.0          1.0   
movement_move_laser                      1.0          1.0          1.0   
variables_get                            NaN          3.0          1.0   
variables_set                            NaN          3.0          1.0   
math_number                              NaN          1.0          1.0   
math_arithmetic                          NaN          1.0          NaN   
movement_rotate_laser                    NaN          1.0          1.0   
movement_laser_change_intensity          NaN          NaN          NaN   
movement_move                            NaN          NaN          NaN   
movement_rotate                          NaN          NaN          NaN   
text                                     NaN          NaN          NaN   
movement_activate_door                   NaN          NaN          NaN   
logic_boolean                            NaN          NaN          NaN   
logic_compare                            NaN          NaN          NaN   
logic_cells_occupied                     NaN          NaN          NaN   
logic_negate                             NaN          NaN          NaN   

                                 variables_6  variables_9  types_4  types_5  \
procedures_callreturn                    NaN          NaN      NaN      NaN   
procedures_callnoreturn                  NaN          NaN      NaN      NaN   
procedures_defreturn                     NaN          NaN      NaN      NaN   
procedures_defnoreturn                   NaN          NaN      NaN      NaN   
start_start                              1.0          1.0      1.0      1.0   
movement_move_laser                      2.0          6.0      NaN      NaN   
variables_get                            1.0          1.0      3.0      1.0   
variables_set                            3.0          3.0      3.0      2.0   
math_number                              1.0          2.0      2.0      1.0   
math_arithmetic                          NaN          NaN      NaN      NaN   
movement_rotate_laser                    1.0          4.0      NaN      NaN   
movement_laser_change_intensity          NaN          1.0      NaN      NaN   
movement_move                            NaN          NaN      4.0      2.0   
movement_rotate                          NaN          NaN      2.0      1.0   
text                                     NaN          NaN      1.0      1.0   
movement_activate_door                   NaN          NaN      NaN      NaN   
logic_boolean                            NaN          NaN      NaN      NaN   
logic_compare                            NaN          NaN      NaN      NaN   
logic_cells_occupied                     NaN          NaN      NaN      NaN   
logic_negate                             NaN          NaN      NaN      NaN   

                                 types_6  types_7  types_8  types_9  types_3  \
procedures_callreturn                NaN      NaN      NaN      NaN      NaN   
procedures_callnoreturn              NaN      NaN      NaN      NaN      NaN   
procedures_defreturn                 NaN      NaN      NaN      NaN      NaN   
procedures_defnoreturn               NaN      NaN      NaN      NaN      NaN   
start_start                          5.0      1.0      1.0      NaN      2.0   
movement_move_laser                  NaN      NaN      NaN      NaN      NaN   
variables_get                        5.0      4.0      3.0      1.0      2.0   
variables_set                        1.0      2.0      5.0      1.0      2.0   
math_number                          1.0      1.0      1.0      1.0      5.0   
math_arithmetic   

In [390]:
outliersMovidas = Outliers(dataMovidas, listaMovidas)
pd.DataFrame(outliersMovidas)

pbgky               auvqa  \
variables_4          {variables_get: 5}                 NaN   
variables_5          {variables_get: 4}  {variables_get: 2}   
types_5              {variables_set: 4}  {variables_get: 2}   
types_8            {movement_rotate: 2}                 NaN   
types_9              {variables_set: 4}                 NaN   
types_6                             NaN    {math_number: 2}   
tutorials_4                         NaN                 NaN   
variables_6                         NaN                 NaN   
types_7                             NaN                 NaN   
variables_7                         NaN                 NaN   
variables_8                         NaN                 NaN   
types_2                             NaN                 NaN   
basic_operators_3                   NaN                 NaN   
basic_operators_7                   NaN                 NaN   
variables_9                         NaN                 NaN   
types_1                             NaN                 NaN   
types_3                             NaN                 NaN   
types_4                             NaN                 NaN   
basic_operators_2                   NaN                 NaN   
basic_operators_4                   NaN                 NaN   
variables_2                         NaN                 NaN   

                                      qeqyj               kmqou  \
variables_4              {variables_set: 4}                 NaN   
variables_5                             NaN  {variables_get: 2}   
types_5                           {text: 3}                 NaN   
types_8                                 NaN                 NaN   
types_9                                 NaN                 NaN   
types_6                                 NaN                 NaN   
tutorials_4        {movement_move_laser: 2}                 NaN   
variables_6                {math_number: 2}                 NaN   
types_7                           {text: 2}                 NaN   
variables_7                             NaN    {start_start: 4}   
variables_8                             NaN    {math_number: 2}   
types_2                                 NaN  {variables_get: 2}   
basic_operators_3                       NaN                 NaN   
basic_operators_7                       NaN                 NaN   
variables_9                             NaN                 NaN   
types_1                                 NaN                 NaN   
types_3                                 NaN                 NaN   
types_4                                 NaN                 NaN   
basic_operators_2                       NaN                 NaN   
basic_operators_4                       NaN                 NaN   
variables_2                             NaN                 NaN   

                                loemd               gcpze               eprdu  \
variables_4                       NaN                 NaN                 NaN   
variables_5        {variables_get: 3}                 NaN                 NaN   
types_5                           NaN           {text: 2}                 NaN   
types_8                           NaN                 NaN                 NaN   
types_9                           NaN  {variables_set: 3}  {variables_set: 2}   
types_6                           NaN                 NaN                 NaN   
tutorials_4                       NaN                 NaN                 NaN   
variables_6        {variables_get: 2}                 NaN                 NaN   
types_7                           NaN                 NaN                 NaN   
variables_7                       NaN                 NaN                 NaN   
variables_8                       NaN                 NaN                 NaN   
types_2                           NaN                 NaN                 NaN   
basic_operators_3                 NaN                 NaN  {variables_get: 3}   
basic_operators_7                 NaN 

In [391]:
pd.DataFrame(dataEliminadas)

gqoj  \
tutorials_2        {'procedures_callreturn': 1, 'procedures_callnoreturn': 1, 'procedures_defreturn': 1, 'procedures_defnoreturn': 1}   
variables_5                                                                                                                       NaN   
variables_9                                                                                                                       NaN   
types_3                                                                                                                           NaN   
types_4                                                                                                                           NaN   
types_5                                                                                                                           NaN   
types_8                                                                                                                           NaN   
types_9                                                                                                                           NaN   
variables_2                                                                                                                       NaN   
types_7                                                                                                                           NaN   
variables_4                                                                                                                       NaN   
basic_operators_4                                                                                                                 NaN   
loops_3                                                                                                                           NaN   
variables_6                                                                                                                       NaN   
variables_7                                                                                                                       NaN   
variables_8                                                                                                                       NaN   
basic_operators_2                                                                                                                 NaN   
basic_operators_5                                                                                                                 NaN   
basic_operators_6                                                                                                                 NaN   
types_6                                                                                                                           NaN   
tutorials_6                                                                                                                       NaN   
tutorials_7                                                                                                                       NaN   
types_2                                                                                                                           NaN   
types_1                                                                                                                           NaN   
variables_3                                                                                                                       NaN   
loops_1                                                                                                                           NaN   
tutorials_4                                                                                                                       NaN   
variables_1                                                                                                                       NaN   
basic_operators_3                                                                                                                 NaN   
loops_4            

In [392]:
mediaEliminadas, listaEliminadas = mediaTarjetas(dataEliminadas)
pd.DataFrame(mediaEliminadas)

tutorials_2  variables_5  variables_9  types_3  \
procedures_callreturn            1.0          NaN          NaN      NaN   
procedures_callnoreturn          1.0          NaN          NaN      NaN   
procedures_defreturn             1.0          NaN          NaN      NaN   
procedures_defnoreturn           1.0          NaN          NaN      NaN   
variables_set                    NaN          1.0          1.0      1.0   
variables_get                    NaN          3.0          3.0      2.0   
math_number                      NaN          1.0          1.0      1.0   
movement_move_laser              NaN          1.0          1.0      NaN   
start_start                      NaN          1.0          1.0      1.0   
movement_rotate_laser            NaN          NaN          1.0      NaN   
text                             NaN          NaN          NaN      1.0   
movement_move                    NaN          NaN          NaN      1.0   
movement_rotate                  NaN          NaN          NaN      1.0   
logic_boolean                    NaN          NaN          NaN      NaN   
movement_activate_door           NaN          NaN          NaN      NaN   
math_arithmetic                  NaN          NaN          NaN      NaN   
logic_compare                    NaN          NaN          NaN      NaN   

                         types_4  types_5  types_8  types_9  variables_2  \
procedures_callreturn        NaN      NaN      NaN      NaN          NaN   
procedures_callnoreturn      NaN      NaN      NaN      NaN          NaN   
procedures_defreturn         NaN      NaN      NaN      NaN          NaN   
procedures_defnoreturn       NaN      NaN      NaN      NaN          NaN   
variables_set                1.0      2.0      1.0      1.0          1.0   
variables_get                1.0      1.0      2.0      1.0          3.0   
math_number                  1.0      1.0      NaN      NaN          NaN   
movement_move_laser          NaN      NaN      NaN      NaN          NaN   
start_start                  NaN      NaN      NaN      NaN          NaN   
movement_rotate_laser        NaN      NaN      NaN      NaN          NaN   
text                         2.0      1.0      1.0      1.0          NaN   
movement_move                1.0      1.0      1.0      1.0          NaN   
movement_rotate              1.0      1.0      1.0      1.0          NaN   
logic_boolean                NaN      NaN      NaN      1.0          NaN   
movement_activate_door       NaN      NaN      NaN      1.0          NaN   
math_arithmetic              NaN      NaN      NaN      NaN          NaN   
logic_compare                NaN      NaN      NaN      NaN          NaN   

                         types_7  variables_4  basic_operators_4  loops_3  \
procedures_callreturn        NaN          NaN                NaN      NaN   
procedures_callnoreturn      NaN          NaN                NaN      NaN   
procedures_defreturn         NaN          NaN                NaN      NaN   
procedures_defnoreturn       NaN          NaN                NaN      NaN   
variables_set                1.0          1.0                1.0      1.0   
variables_get                2.0          1.0                3.0      1.0   
math_number                  1.0          1.0                NaN      1.0   
movement_move_laser          NaN          NaN                NaN      NaN   
start_start                  NaN          NaN                NaN      NaN   
movement_rotate_laser        NaN          NaN                NaN      NaN   
text                         1.0          NaN                NaN      NaN   
movement_move                1.0          NaN                8.0      NaN   
movement_rotate              1.0          NaN                NaN      NaN   
logic_boolean                1.0          NaN                NaN      NaN   
movement_activate_door       NaN          NaN                NaN      NaN   
math_arithmetic              NaN          NaN                1.0      NaN

In [393]:
outliersEliminadas = Outliers(dataEliminadas, listaEliminadas)
pd.DataFrame(outliersEliminadas)

pbgky               gcpze               eprdu  \
types_5            {movement_move: 2}  {movement_move: 2}                 NaN   
basic_operators_4                 NaN  {variables_get: 5}                 NaN   
variables_4                       NaN                 NaN  {variables_get: 2}   
variables_7                       NaN                 NaN                 NaN   
types_6                           NaN                 NaN                 NaN   
variables_6                       NaN                 NaN                 NaN   
types_3                           NaN                 NaN                 NaN   
types_4                           NaN                 NaN                 NaN   
variables_5                       NaN                 NaN                 NaN   
types_7                           NaN                 NaN                 NaN   
basic_operators_2                 NaN                 NaN                 NaN   
variables_8                       NaN                 NaN                 NaN   
variables_9                       NaN                 NaN                 NaN   
basic_operators_3                 NaN                 NaN                 NaN   
types_9                           NaN                 NaN                 NaN   
variables_2                       NaN                 NaN                 NaN   
types_1                           NaN                 NaN                 NaN   
types_8                           NaN                 NaN                 NaN   

                                qeqyj                     sxipu  \
types_5            {variables_get: 2}                       NaN   
basic_operators_4                 NaN                       NaN   
variables_4        {variables_get: 5}        {variables_get: 2}   
variables_7        {variables_set: 2}                       NaN   
types_6            {variables_get: 2}                       NaN   
variables_6                       NaN  {movement_move_laser: 2}   
types_3                           NaN        {variables_get: 4}   
types_4                           NaN        {variables_get: 2}   
variables_5                       NaN                       NaN   
types_7                           NaN                       NaN   
basic_operators_2                 NaN                       NaN   
variables_8                       NaN                       NaN   
variables_9                       NaN                       NaN   
basic_operators_3                 NaN                       NaN   
types_9                           NaN                       NaN   
variables_2                       NaN                       NaN   
types_1                           NaN                       NaN   
types_8                           NaN                       NaN   

                                vsxld               ipdcp               ejeuw  \
types_5                           NaN                 NaN                 NaN   
basic_operators_4                 NaN                 NaN                 NaN   
variables_4                       NaN  {variables_get: 3}  {variables_set: 3}   
variables_7                       NaN                 NaN                 NaN   
types_6            {variables_get: 2}                 NaN                 NaN   
variables_6        {variables_set: 2}                 NaN  {variables_set: 2}   
types_3                           NaN                 NaN                 NaN   
types_4                           NaN  {variables_get: 2}                 NaN   
variables_5        {variables_set: 2}                 NaN                 NaN   
types_7                           NaN                 NaN                 NaN   
basic_operators_2                 NaN                 NaN                 NaN   
variables_8                       NaN                 NaN                 NaN   
variables_9                       NaN                 NaN                 NaN   
basic_operators_3                 NaN                 NaN                 NaN   
typ

In [394]:
pd.DataFrame(dataAttach)

pbgky  \
variables_2                                                                                              {'movement_move_laser': 4, 'variables_set': 1, 'movement_rotate_laser': 1}   
variables_3                                                                                                                                                      {'math_number': 1}   
variables_4                                                                                                                        {'movement_rotate_laser': 1, 'variables_get': 1}   
variables_5                                                        {'variables_set': 7, 'variables_get': 7, 'math_number': 2, 'movement_rotate_laser': 4, 'movement_move_laser': 7}   
variables_6                                                                         {'variables_set': 3, 'movement_move_laser': 10, 'variables_get': 7, 'movement_rotate_laser': 4}   
variables_7                                                                                              {'movement_move_laser': 2, 'variables_get': 3, 'movement_rotate_laser': 3}   
variables_8                                                                                                              {'variables_get': 3, 'variables_set': 1, 'math_number': 1}   
variables_9                                                                          {'movement_move_laser': 2, 'variables_get': 3, 'variables_set': 1, 'movement_rotate_laser': 1}   
types_1                                                                                                  {'movement_move_laser': 1, 'variables_get': 2, 'movement_rotate_laser': 1}   
types_2                                                                                                                                                          {'math_number': 1}   
types_3                                                             {'movement_rotate': 1, 'text': 1, 'math_number': 2, 'movement_move': 1, 'variables_get': 4, 'variables_set': 1}   
types_4                                                                        {'variables_set': 2, 'movement_rotate': 2, 'math_number': 2, 'variables_get': 8, 'movement_move': 3}   
types_5                                                            {'variables_set': 9, 'math_number': 1, 'text': 3, 'variables_get': 10, 'movement_move': 3, 'movement_rotate': 5}   
types_6                                                             {'variables_set': 3, 'text': 1, 'math_number': 1, 'movement_move': 1, 'variables_get': 4, 'movement_rotate': 1}   
types_7                              {'variables_set': 3, 'text': 3, 'movement_activate_door': 1, 'variables_get': 8, 'logic_boolean': 1, 'movement_move': 2, 'movement_rotate': 1}   
types_8                                                            {'variables_set': 2, 'text': 1, 'math_number': 1, 'variables_get': 10, 'movement_rotate': 3, 'movement_move': 2}   
types_9            {'variables_set': 3, 'logic_boolean': 1, 'text': 1, 'movement_move': 4, 'math_number': 1, 'variables_get': 7, 'movement_rotate': 1, 'movement_activate_door': 1}   
tutorials_2                                                                                                                                                                     NaN   
tutorials_4                                                                                                                                                                     NaN   
tutorials_1                                                                                                                                                                     NaN   
tutorials_7                                                                                                                                                                     NaN   
basic_operators_2                                                                                                                                   

In [395]:
mediaAttach, listaAttach = mediaTarjetas(dataAttach)
pd.DataFrame(mediaAttach)

variables_2  variables_3  variables_4  \
movement_move_laser                      1.0          2.0          1.0   
variables_set                            2.0          1.0          1.0   
movement_rotate_laser                    1.0          1.0          1.0   
math_number                              1.0          1.0          4.0   
variables_get                            1.0          4.0          1.0   
start_start                              1.0          NaN          1.0   
logic_ifelse                             NaN          NaN          1.0   
movement_rotate                          NaN          NaN          NaN   
movement_move                            NaN          NaN          NaN   
text                                     NaN          NaN          NaN   
movement_activate_door                   NaN          NaN          NaN   
logic_boolean                            NaN          NaN          NaN   
movement_laser_change_intensity          NaN          NaN          NaN   
logic_compare                            NaN          NaN          NaN   
math_arithmetic                          NaN          NaN          NaN   
logic_cells_occupied                     NaN          NaN          NaN   
logic_operation                          NaN          NaN          NaN   
logic_negate                             NaN          NaN          NaN   

                                 variables_5  variables_6  variables_7  \
movement_move_laser                      4.0          5.0          4.0   
variables_set                            5.0          3.0          2.0   
movement_rotate_laser                    3.0          1.0          1.0   
math_number                              1.0          1.0          3.0   
variables_get                            6.0          4.0          4.0   
start_start                              2.0          1.0          NaN   
logic_ifelse                             NaN          NaN          NaN   
movement_rotate                          NaN          1.0          NaN   
movement_move                            NaN          NaN          NaN   
text                                     NaN          NaN          NaN   
movement_activate_door                   NaN          NaN          NaN   
logic_boolean                            NaN          NaN          NaN   
movement_laser_change_intensity          NaN          NaN          NaN   
logic_compare                            NaN          NaN          NaN   
math_arithmetic                          NaN          NaN          NaN   
logic_cells_occupied                     NaN          NaN          NaN   
logic_operation                          NaN          NaN          NaN   
logic_negate                             NaN          NaN          NaN   

                                 variables_8  variables_9  types_1  types_2  \
movement_move_laser                      1.0          2.0      3.0      NaN   
variables_set                            1.0          1.0      1.0      3.0   
movement_rotate_laser                    1.0          1.0      3.0      NaN   
math_number                              1.0          2.0      3.0      1.0   
variables_get                            4.0          3.0      3.0      1.0   
start_start                              2.0          1.0      NaN      1.0   
logic_ifelse                             NaN          NaN      NaN      NaN   
movement_rotate                          1.0          NaN      1.0      NaN   
movement_move                            1.0          NaN      NaN      1.0   
text                                     NaN          NaN      NaN      1.0   
movement_activate_door                   NaN          NaN      NaN      NaN   
logic_boolean                            NaN          NaN      NaN      NaN   
movement_laser_change_intensity          NaN          NaN      NaN      NaN   
logic_compare                            NaN          NaN      NaN      NaN   
math_arithmetic                   

In [396]:
outliersAttach = Outliers(dataAttach, listaAttach)
pd.DataFrame(outliersAttach)

pbgky                 auvqa  \
variables_2          {movement_move_laser: 4}                   NaN   
variables_5          {movement_move_laser: 7}      {math_number: 3}   
variables_6        {movement_rotate_laser: 4}                   NaN   
variables_7        {movement_rotate_laser: 3}                   NaN   
types_3                      {math_number: 2}    {variables_set: 2}   
types_4                    {movement_move: 3}    {movement_move: 3}   
types_5                  {movement_rotate: 5}             {text: 3}   
types_7                    {variables_get: 8}                   NaN   
types_8                    {movement_move: 2}                   NaN   
types_9                    {variables_get: 7}                   NaN   
variables_3                               NaN      {math_number: 2}   
variables_9                               NaN    {variables_get: 5}   
types_6                                   NaN  {movement_rotate: 3}   
tutorials_4                               NaN                   NaN   
variables_4                               NaN                   NaN   
variables_8                               NaN                   NaN   
types_2                                   NaN                   NaN   
basic_operators_2                         NaN                   NaN   
basic_operators_4                         NaN                   NaN   
basic_operators_5                         NaN                   NaN   
basic_operators_6                         NaN                   NaN   
loops_1                                   NaN                   NaN   
loops_3                                   NaN                   NaN   
basic_operators_7                         NaN                   NaN   
types_1                                   NaN                   NaN   
tutorials_7                               NaN                   NaN   
basic_operators_3                         NaN                   NaN   
loops_2                                   NaN                   NaN   

                                                  qeqyj  \
variables_2                                         NaN   
variables_5                                         NaN   
variables_6                  {movement_rotate_laser: 4}   
variables_7                  {movement_rotate_laser: 2}   
types_3                              {variables_get: 9}   
types_4                              {movement_move: 3}   
types_5                             {variables_get: 13}   
types_7                              {variables_get: 5}   
types_8                            {movement_rotate: 2}   
types_9                              {variables_set: 2}   
variables_3                                         NaN   
variables_9                          {variables_set: 2}   
types_6                              {variables_get: 5}   
tutorials_4        {movement_laser_change_intensity: 2}   
variables_4                    {movement_move_laser: 4}   
variables_8                          {variables_get: 5}   
types_2                                             NaN   
basic_operators_2                                   NaN   
basic_operators_4                                   NaN   
basic_operators_5                                   NaN   
basic_operators_6                                   NaN   
loops_1                                             NaN   
loops_3                                             NaN   
basic_operators_7                                   NaN   
types_1                                             NaN   
tutorials_7                                         NaN   
basic_operators_3                                   NaN   
loops_2                                             NaN   

                                      kmqou                 ikcar  \
variables_2                             NaN                   NaN   
variables_5                {math_number: 2}      {math_number: 5}   
variables_6                             NaN                  

In [397]:
pd.DataFrame(dataDettach)

pbgky  \
variables_2                                                        {'movement_move_laser': 1}   
variables_5              {'variables_set': 1, 'movement_rotate_laser': 1, 'variables_get': 1}   
variables_6        {'movement_move_laser': 1, 'movement_rotate_laser': 1, 'variables_set': 1}   
variables_9                                                              {'variables_set': 1}   
types_3                                                                           {'text': 1}   
types_4                                                                  {'variables_set': 1}   
types_5                        {'variables_set': 3, 'movement_move': 2, 'movement_rotate': 1}   
types_7                                                                {'movement_rotate': 1}   
types_8                                                                {'movement_rotate': 1}   
types_9                          {'variables_set': 1, 'movement_move': 1, 'logic_boolean': 1}   
types_6                                                                                   NaN   
tutorials_2                                                                               NaN   
tutorials_4                                                                               NaN   
variables_4                                                                               NaN   
variables_7                                                                               NaN   
variables_8                                                                               NaN   
types_1                                                                                   NaN   
basic_operators_2                                                                         NaN   
basic_operators_3                                                                         NaN   
basic_operators_5                                                                         NaN   
basic_operators_6                                                                         NaN   
basic_operators_7                                                                         NaN   
loops_1                                                                                   NaN   
basic_operators_4                                                                         NaN   
loops_3                                                                                   NaN   
tutorials_6                                                                               NaN   
tutorials_7                                                                               NaN   
types_2                                                                                   NaN   
variables_1                                                                               NaN   
variables_3                                                                               NaN   
loops_4                                                                                   NaN   
basic_operators_1                                                                         NaN   
tutorials_3                                                                               NaN   
tutorials_1                                                                               NaN   

                                                                          auvqa  \
variables_2                                                                 NaN   
variables_5                                                {'variables_set': 1}   
variables_6                                                                 NaN   
variables_9                                                {'variables_set': 1}   
types_3                                                             {'text': 3}   
types_4                                                                     NaN   
types_5                                                             {'text': 2}   
types_7                     

In [398]:
mediaDettach, listaDettach = mediaTarjetas(dataDettach)
pd.DataFrame(mediaDettach)

variables_2  variables_5  variables_6  \
movement_move_laser                      2.0          1.0          4.0   
variables_set                            2.0          1.0          3.0   
variables_get                            1.0          3.0          1.0   
movement_rotate_laser                    1.0          1.0          1.0   
math_number                              3.0          2.0          1.0   
text                                     NaN          NaN          NaN   
movement_move                            NaN          NaN          NaN   
movement_rotate                          NaN          NaN          NaN   
logic_boolean                            NaN          NaN          NaN   
movement_activate_door                   NaN          NaN          NaN   
movement_laser_change_intensity          NaN          NaN          NaN   
logic_compare                            NaN          NaN          NaN   
math_arithmetic                          NaN          NaN          NaN   
logic_operation                          NaN          NaN          NaN   
logic_negate                             NaN          NaN          NaN   

                                 variables_9  types_3  types_4  types_5  \
movement_move_laser                      2.0      NaN      NaN      NaN   
variables_set                            1.0      1.0      1.0      2.0   
variables_get                            2.0      2.0      1.0      1.0   
movement_rotate_laser                    1.0      1.0      NaN      NaN   
math_number                              1.0      2.0      1.0      2.0   
text                                     NaN      3.0      2.0      2.0   
movement_move                            NaN      1.0      1.0      1.0   
movement_rotate                          NaN      1.0      1.0      1.0   
logic_boolean                            NaN      NaN      NaN      NaN   
movement_activate_door                   NaN      NaN      NaN      NaN   
movement_laser_change_intensity          NaN      NaN      NaN      NaN   
logic_compare                            NaN      NaN      NaN      NaN   
math_arithmetic                          NaN      NaN      NaN      NaN   
logic_operation                          NaN      NaN      NaN      NaN   
logic_negate                             NaN      NaN      NaN      NaN   

                                 types_7  types_8  types_9  types_6  \
movement_move_laser                  NaN      NaN      NaN      NaN   
variables_set                        2.0      1.0      1.0      1.0   
variables_get                        1.0      1.0      1.0      6.0   
movement_rotate_laser                NaN      NaN      NaN      NaN   
math_number                          1.0      1.0      1.0      1.0   
text                                 1.0      1.0      NaN      1.0   
movement_move                        1.0      2.0      1.0      1.0   
movement_rotate                      1.0      1.0      3.0      1.0   
logic_boolean                        1.0      NaN      1.0      NaN   
movement_activate_door               1.0      NaN      1.0      1.0   
movement_laser_change_intensity      NaN      NaN      NaN      NaN   
logic_compare                        NaN      NaN      NaN      NaN   
math_arithmetic                      NaN      NaN      NaN      NaN   
logic_operation                      NaN      NaN      NaN      NaN   
logic_negate                         NaN      NaN      NaN      NaN   

                                 tutorials_2  tutorials_4  variables_4  \
movement_move_laser                      2.0          1.0          1.0   
variables_set                            NaN          NaN          1.0   
variables_get                            NaN          NaN          1.0   
movement_rotate_laser                    NaN          NaN          1.0   
math_number                              NaN          1.0          1.0   
text                                     NaN          NaN         

In [399]:
outliersDettach = Outliers(dataDettach, listaDettach)
pd.DataFrame(outliersDettach)

pbgky                     qeqyj  \
types_5            {movement_move: 2}      {movement_rotate: 2}   
tutorials_4                       NaN  {movement_move_laser: 3}   
variables_4                       NaN        {variables_set: 3}   
variables_6                       NaN        {variables_get: 2}   
variables_7                       NaN        {variables_set: 2}   
variables_9                       NaN        {variables_set: 2}   
types_9                           NaN        {movement_move: 2}   
variables_2                       NaN                       NaN   
basic_operators_2                 NaN                       NaN   
variables_5                       NaN                       NaN   
types_6                           NaN                       NaN   
types_3                           NaN                       NaN   
variables_8                       NaN                       NaN   
types_4                           NaN                       NaN   
types_7                           NaN                       NaN   
tutorials_7                       NaN                       NaN   
types_1                           NaN                       NaN   
basic_operators_3                 NaN                       NaN   
basic_operators_5                 NaN                       NaN   
types_2                           NaN                       NaN   
types_8                           NaN                       NaN   
variables_3                       NaN                       NaN   
basic_operators_4                 NaN                       NaN   

                                loemd               ftpnb               eprdu  \
types_5                           NaN                 NaN                 NaN   
tutorials_4                       NaN                 NaN                 NaN   
variables_4                       NaN                 NaN  {variables_set: 2}   
variables_6                       NaN                 NaN                 NaN   
variables_7                       NaN                 NaN                 NaN   
variables_9                       NaN                 NaN                 NaN   
types_9                           NaN                 NaN                 NaN   
variables_2        {variables_get: 2}                 NaN                 NaN   
basic_operators_2                 NaN  {variables_set: 3}                 NaN   
variables_5                       NaN                 NaN                 NaN   
types_6                           NaN                 NaN                 NaN   
types_3                           NaN                 NaN                 NaN   
variables_8                       NaN                 NaN                 NaN   
types_4                           NaN                 NaN                 NaN   
types_7                           NaN                 NaN                 NaN   
tutorials_7                       NaN                 NaN                 NaN   
types_1                           NaN                 NaN                 NaN   
basic_operators_3                 NaN                 NaN                 NaN   
basic_operators_5                 NaN                 NaN                 NaN   
types_2                           NaN                 NaN                 NaN   
types_8                           NaN                 NaN                 NaN   
variables_3                       NaN                 NaN                 NaN   
basic_operators_4                 NaN                 NaN                 NaN   

                                      gcpze               gleqe  \
types_5                                 NaN                 NaN   
tutorials_4                             NaN                 NaN   
variables_4                             NaN  {variables_set: 2}   
variables_6                             NaN                 NaN   
variables_7                             NaN                 NaN   
variables_9                             NaN                 NaN   
types_9  

In [400]:
pd.DataFrame(dataDuplicate)

gcpze  \
variables_7                        {'movement_move_laser': 1}   
variables_9                        {'movement_move_laser': 2}   
types_4            {'movement_move': 1, 'movement_rotate': 1}   
types_5            {'movement_rotate': 1, 'movement_move': 1}   
types_7                                  {'movement_move': 1}   
types_8                                {'movement_rotate': 1}   
types_9                                  {'movement_move': 1}   
loops_1                                  {'movement_move': 3}   
variables_6                                               NaN   
variables_4                                               NaN   
basic_operators_4                                         NaN   
loops_3                                                   NaN   
variables_8                                               NaN   
types_1                                                   NaN   
types_2                                                   NaN   
types_3                                                   NaN   
basic_operators_3                                         NaN   
tutorials_7                                               NaN   
types_6                                                   NaN   
basic_operators_2                                         NaN   
basic_operators_7                                         NaN   
loops_2                                                   NaN   
variables_3                                               NaN   
variables_5                                               NaN   

                                        khadt                 epqkm  \
variables_7                               NaN                   NaN   
variables_9                               NaN                   NaN   
types_4                                   NaN                   NaN   
types_5                                   NaN                   NaN   
types_7                                   NaN                   NaN   
types_8                                   NaN                   NaN   
types_9                                   NaN                   NaN   
loops_1                                   NaN                   NaN   
variables_6        {'movement_move_laser': 2}                   NaN   
variables_4                               NaN  {'variables_set': 1}   
basic_operators_4                         NaN                   NaN   
loops_3                                   NaN                   NaN   
variables_8                               NaN                   NaN   
types_1                                   NaN                   NaN   
types_2                                   NaN                   NaN   
types_3                                   NaN                   NaN   
basic_operators_3                         NaN                   NaN   
tutorials_7                               NaN                   NaN   
types_6                                   NaN                   NaN   
basic_operators_2                         NaN                   NaN   
basic_operators_7                         NaN                   NaN   
loops_2                                   NaN                   NaN   
variables_3                               NaN                   NaN   
variables_5                               NaN                   NaN   

                                        eprdu                       cmbfi  \
variables_7        {'movement_move_laser': 2}                         NaN   
variables_9        {'movement_move_laser': 2}                         NaN   
types_4                                   NaN                         NaN   
types_5                                   NaN                         NaN   
types_7                  {'movement_move': 1}                         NaN   
types_8                                   NaN                         NaN   
types_9                                   NaN                         NaN   
loops_1                  {'movement_mo

In [401]:
mediaDuplicate, listaDuplicate = mediaTarjetas(dataDuplicate)
pd.DataFrame(mediaDuplicate)

variables_7  variables_9  types_4  types_5  types_7  \
movement_move_laser            2.0          2.0      NaN      NaN      NaN   
variables_get                  1.0          2.0      3.0      3.0      1.0   
variables_set                  1.0          1.0      NaN      3.0      3.0   
movement_move                  NaN          NaN      1.0      1.0      1.0   
movement_rotate                NaN          NaN      1.0      1.0      NaN   
text                           NaN          NaN      NaN      2.0      1.0   
math_number                    NaN          NaN      NaN      NaN      NaN   
movement_rotate_laser          NaN          NaN      NaN      NaN      NaN   
math_arithmetic                NaN          NaN      NaN      NaN      NaN   

                       types_8  types_9  loops_1  variables_6  variables_4  \
movement_move_laser        NaN      NaN      NaN          3.0          NaN   
variables_get              5.0      1.0      8.0          2.0          1.0   
variables_set              1.0      NaN      1.0          1.0          2.0   
movement_move              NaN      1.0      3.0          NaN          NaN   
movement_rotate            1.0      NaN      NaN          NaN          NaN   
text                       NaN      NaN      NaN          NaN          NaN   
math_number                NaN      1.0      NaN          NaN          NaN   
movement_rotate_laser      NaN      NaN      NaN          1.0          NaN   
math_arithmetic            NaN      NaN      NaN          NaN          NaN   

                       basic_operators_4  loops_3  variables_8  types_1  \
movement_move_laser                  NaN      NaN          1.0      NaN   
variables_get                        2.0      4.0          2.0      1.0   
variables_set                        2.0      NaN          NaN      NaN   
movement_move                        4.0      2.0          NaN      NaN   
movement_rotate                      NaN      NaN          NaN      NaN   
text                                 2.0      NaN          NaN      NaN   
math_number                          NaN      NaN          NaN      NaN   
movement_rotate_laser                NaN      NaN          NaN      NaN   
math_arithmetic                      NaN      NaN          NaN      NaN   

                       types_2  types_3  basic_operators_3  tutorials_7  \
movement_move_laser        NaN      NaN                NaN          3.0   
variables_get              2.0      4.0                2.0          NaN   
variables_set              NaN      1.0                NaN          NaN   
movement_move              NaN      NaN                NaN          NaN   
movement_rotate            NaN      NaN                NaN          NaN   
text                       NaN      1.0                1.0          NaN   
math_number                NaN      NaN                NaN          NaN   
movement_rotate_laser      NaN      NaN                NaN          NaN   
math_arithmetic            NaN      NaN                1.0          NaN   

                       types_6  basic_operators_2  basic_operators_7  loops_2  \
movement_move_laser        NaN                NaN                NaN      NaN   
variables_get              3.0                1.0                NaN      2.0   
variables_set              NaN                NaN                NaN      NaN   
movement_move              1.0                NaN                NaN      NaN   
movement_rotate            1.0                NaN                NaN      NaN   
text                       1.0                NaN                1.0      NaN   
math_number                1.0                NaN                NaN      NaN   
movement_rotate_laser      NaN                NaN                NaN      NaN   
math_arithmetic            NaN                NaN                NaN      NaN   

                       variables_3  variables_5  
movement_move_laser            NaN          NaN  
variables_get                  NaN          1.0 

In [402]:
outliersDuplicate = Outliers(dataDuplicate, listaDuplicate)
pd.DataFrame(outliersDuplicate)

dunul               kmqou  \
variables_9         {variables_get: 5}                 NaN   
types_1             {variables_get: 3}                 NaN   
types_5             {variables_get: 9}  {movement_move: 2}   
types_9            {variables_get: 15}                 NaN   
basic_operators_4   {variables_get: 8}                 NaN   
types_4                            NaN  {movement_move: 2}   
variables_6                        NaN                 NaN   
types_7                            NaN                 NaN   
types_8                            NaN                 NaN   
basic_operators_2                  NaN                 NaN   
basic_operators_3                  NaN                 NaN   

                                      fivin               mgaak  \
variables_9                             NaN                 NaN   
types_1                                 NaN                 NaN   
types_5                                 NaN  {variables_get: 5}   
types_9                                 NaN  {variables_get: 2}   
basic_operators_4                       NaN  {variables_get: 6}   
types_4                                 NaN  {variables_get: 7}   
variables_6        {movement_move_laser: 4}                 NaN   
types_7                                 NaN           {text: 2}   
types_8                                 NaN  {variables_get: 7}   
basic_operators_2                       NaN  {variables_get: 3}   
basic_operators_3                       NaN  {variables_get: 3}   

                                      pzfdd               icllt  \
variables_9                             NaN                 NaN   
types_1                                 NaN                 NaN   
types_5                                 NaN                 NaN   
types_9                                 NaN                 NaN   
basic_operators_4                       NaN                 NaN   
types_4                                 NaN                 NaN   
variables_6        {movement_move_laser: 8}  {variables_set: 2}   
types_7                                 NaN                 NaN   
types_8                                 NaN                 NaN   
basic_operators_2                       NaN                 NaN   
basic_operators_3                       NaN                 NaN   

                                pqwaf  
variables_9                       NaN  
types_1                           NaN  
types_5                           NaN  
types_9                           NaN  
basic_operators_4                 NaN  
types_4                           NaN  
variables_6                       NaN  
types_7            {variables_get: 2}  
types_8                           NaN  
basic_operators_2                 NaN  
basic_operators_3                 NaN

In [403]:
pd.DataFrame(dataDeclare)

pbgky            auvqa            eprdu  \
variables_5        {'variable': 3}  {'variable': 1}  {'variable': 1}   
types_4            {'variable': 1}  {'variable': 2}  {'variable': 1}   
types_5            {'variable': 4}  {'variable': 4}  {'variable': 1}   
types_7            {'variable': 3}  {'variable': 2}              NaN   
types_8            {'variable': 2}              NaN  {'variable': 2}   
types_9            {'variable': 2}              NaN  {'variable': 1}   
variables_8                    NaN  {'variable': 1}  {'variable': 1}   
variables_9                    NaN  {'variable': 1}              NaN   
types_6                        NaN  {'variable': 2}              NaN   
variables_4                    NaN              NaN  {'variable': 2}   
variables_6                    NaN              NaN  {'variable': 1}   
basic_operators_3              NaN              NaN  {'variable': 1}   
basic_operators_4              NaN              NaN  {'variable': 3}   
loops_1                        NaN              NaN  {'variable': 2}   
basic_operators_7              NaN              NaN              NaN   
types_2                        NaN              NaN              NaN   
types_3                        NaN              NaN              NaN   
variables_7                    NaN              NaN              NaN   
basic_operators_2              NaN              NaN              NaN   
loops_4                        NaN              NaN              NaN   
types_1                        NaN              NaN              NaN   
basic_operators_5              NaN              NaN              NaN   
basic_operators_6              NaN              NaN              NaN   

                             gcpze            ipdcp            xnpqf  \
variables_5        {'variable': 1}  {'variable': 5}              NaN   
types_4            {'variable': 1}  {'variable': 3}  {'variable': 1}   
types_5            {'variable': 1}  {'variable': 3}  {'variable': 3}   
types_7                        NaN              NaN  {'variable': 2}   
types_8            {'variable': 2}              NaN              NaN   
types_9            {'variable': 1}              NaN              NaN   
variables_8                    NaN  {'variable': 1}              NaN   
variables_9                    NaN              NaN              NaN   
types_6                        NaN  {'variable': 1}              NaN   
variables_4                    NaN  {'variable': 1}  {'variable': 1}   
variables_6                    NaN              NaN              NaN   
basic_operators_3  {'variable': 1}              NaN              NaN   
basic_operators_4  {'variable': 5}              NaN              NaN   
loops_1            {'variable': 2}              NaN              NaN   
basic_operators_7  {'variable': 1}              NaN              NaN   
types_2                        NaN  {'variable': 1}              NaN   
types_3                        NaN              NaN              NaN   
variables_7                    NaN              NaN              NaN   
basic_operators_2              NaN              NaN              NaN   
loops_4                        NaN              NaN              NaN   
types_1                        NaN              NaN              NaN   
basic_operators_5              NaN              NaN              NaN   
basic_operators_6              NaN              NaN              NaN   

                             ftpnb            qeqyj            ikcar  \
variables_5                    NaN  {'variable': 1}              NaN   
types_4            {'variable': 1}  {'variable': 1}              NaN   
types_5            {'variable': 1}  {'variable': 2}  {'variable': 2}   
types_7                        NaN  {'variable': 3}  {'variable': 1}   
types_8            {'variable': 2}  {'variable': 2}              NaN   
types_9                        NaN  {'variable': 2}              NaN   
variables_8                    NaN  {'variable': 1}              Na

In [404]:
mediaDeclare, listaDeclare = mediaTarjetas(dataDeclare)
pd.DataFrame(mediaDeclare)

variables_5  types_4  types_5  types_7  types_8  types_9  \
variable          1.0      1.0      4.0      2.0      2.0      1.0   

          variables_8  variables_9  types_6  variables_4  variables_6  \
variable          1.0          1.0      2.0          1.0          2.0   

          basic_operators_3  basic_operators_4  loops_1  basic_operators_7  \
variable                1.0                6.0      2.0                2.0   

          types_2  types_3  variables_7  basic_operators_2  loops_4  types_1  \
variable      3.0      1.0          1.0                2.0      4.0      1.0   

          basic_operators_5  basic_operators_6  
variable                1.0                1.0

In [405]:
outliersDeclare= Outliers(dataDeclare, listaDeclare)
pd.DataFrame(outliersDeclare)

pbgky          auvqa          eprdu          ipdcp  \
variables_5        {variable: 3}            NaN            NaN  {variable: 5}   
types_7            {variable: 3}            NaN            NaN            NaN   
types_9            {variable: 2}            NaN            NaN            NaN   
types_4                      NaN  {variable: 2}            NaN  {variable: 3}   
variables_4                  NaN            NaN  {variable: 2}            NaN   
variables_8                  NaN            NaN            NaN            NaN   
variables_9                  NaN            NaN            NaN            NaN   
types_5                      NaN            NaN            NaN            NaN   
types_8                      NaN            NaN            NaN            NaN   
basic_operators_3            NaN            NaN            NaN            NaN   
basic_operators_2            NaN            NaN            NaN            NaN   
variables_6                  NaN            NaN            NaN            NaN   
variables_7                  NaN            NaN            NaN            NaN   
types_3                      NaN            NaN            NaN            NaN   
types_6                      NaN            NaN            NaN            NaN   

                           qeqyj          hjpbw          fkmtp          kmqou  \
variables_5                  NaN  {variable: 4}  {variable: 2}            NaN   
types_7            {variable: 3}            NaN            NaN            NaN   
types_9            {variable: 2}            NaN            NaN            NaN   
types_4                      NaN            NaN            NaN  {variable: 5}   
variables_4        {variable: 3}            NaN            NaN            NaN   
variables_8                  NaN            NaN            NaN  {variable: 3}   
variables_9                  NaN            NaN            NaN  {variable: 2}   
types_5                      NaN            NaN            NaN  {variable: 5}   
types_8                      NaN            NaN            NaN            NaN   
basic_operators_3            NaN            NaN            NaN            NaN   
basic_operators_2            NaN            NaN            NaN            NaN   
variables_6                  NaN            NaN            NaN            NaN   
variables_7                  NaN            NaN            NaN            NaN   
types_3                      NaN            NaN            NaN            NaN   
types_6                      NaN            NaN            NaN            NaN   

                           ejeuw          bdwyj          epqkm          zwzfv  \
variables_5        {variable: 2}  {variable: 9}  {variable: 3}  {variable: 2}   
types_7                      NaN            NaN            NaN            NaN   
types_9                      NaN            NaN            NaN            NaN   
types_4                      NaN            NaN            NaN            NaN   
variables_4                  NaN            NaN            NaN            NaN   
variables_8                  NaN            NaN            NaN            NaN   
variables_9                  NaN            NaN            NaN            NaN   
types_5                      NaN            NaN            NaN            NaN   
types_8                      NaN            NaN            NaN            NaN   
basic_operators_3            NaN            NaN            NaN            NaN   
basic_operators_2            NaN            NaN            NaN            NaN   
variables_6                  NaN            NaN            NaN            NaN   
variables_7                  NaN            NaN            NaN            NaN   
types_3                      NaN            NaN            NaN            NaN   
types_6                      NaN            NaN            NaN            NaN   

                           asopk          krahz          bhyhw          kkoif  \
variables_5        {variable: 2}            NaN        